Loading Libraries

In [0]:
from pyspark.sql.functions import *
from pyspark.sql.types import *

In [0]:
dbutils.widgets.text("init_load_flag", "0")
init_load_flag = int(dbutils.widgets.get("init_load_flag"))

#### Data Reading

## SOURCE FILE -> Silver_Customers

In [0]:
df = spark.sql("select * from databricks_etl_catalog.silver.customer_silver")
df.display()

customer_id email city state domains full_name C00001 rushjeff@ryan.org Johnsonmouth MS ryan.org Emily Mooney C00002 mccoykiara@kelly.com Stephenfort WY kelly.com Andrea Sellers C00003 rebeccamiller@yahoo.com South Stephenshire LA yahoo.com Craig Hayes C00004 lawrence05@campbell.info Chrisland ND campbell.info Bryan Scott C00005 carrie45@yahoo.com East Dennistown RI yahoo.com Sean Vasquez C00006 traceyramos@gmail.com North Matthew IN gmail.com Kevin Mccarthy C00007 scottallen@gmail.com Joneshaven VA gmail.com Amanda Doyle C00008 sullivanjeremy@horton-adams.com South Nathanfurt CT horton-adams.com Paul Campos C00009 dennis03@yahoo.com Kimberlyview MD yahoo.com Mary Green C00010 charles58@murillo.net West Hector OK murillo.net James Myers C00011 anita65@gmail.com Houstonfurt AR gmail.com Jacob Le C00012 beardtravis@gmail.com East Jenniferview WI gmail.com Chad Banks C00013 jwood@gmail.com Lake Gregoryshire OR gmail.com James Martin C00014 lmoore@yahoo.com East Tiffanybury MS yahoo.com Thomas Hartman C00015 daniellowe@hotmail.com South Courtney SC hotmail.com Diane Harris C00016 amylam@collins.org Jesusburgh IA collins.org Brett Parker C00017 rhondaferguson@gmail.com West Loriborough GA gmail.com Angela Carter C00018 martinfrank@brooks.info Lake Joshuamouth OH brooks.info Darrell Chang C00019 russelltimothy@simpson-hunter.com East Anthonyland NY simpson-hunter.com Angie King C00020 rojassandra@hotmail.com South Oscar NV hotmail.com Juan Collins C00021 morgancraig@stephens.com South Charles ND stephens.com Brian Hawkins C00022 pshepherd@walker-kelly.com Harrisland TN walker-kelly.com Jeanne Hahn C00023 greg64@banks.com North Kara NM banks.com Jackie Stewart C00024 andreawilliams@yahoo.com Stewartport NM yahoo.com Heather Owens C00025 dawn65@yahoo.com Port Juliebury IN yahoo.com Christina Bennett C00026 rebecca20@yahoo.com Ortizshire WY yahoo.com Mark Harris C00027 ashley08@mckinney.info Mosleyburgh NM mckinney.info Brandy Juarez C00028 steven27@gmail.com North Gregoryfurt NM gmail.com Barry Baker C00029 irandall@camacho-smith.com Kaiserhaven OR camacho-smith.com Michael Johnson C00030 cfuller@gmail.com Port Coltonton AL gmail.com Holly Collins C00031 kramerkaylee@hotmail.com Travisview CT hotmail.com Jeanette Smith C00032 egallegos@gmail.com Samuelshire KS gmail.com Alexandria Singleton C00033 lindasummers@hotmail.com South Andrewchester CO hotmail.com Carrie Wheeler C00034 stacy78@gmail.com Gregorybury IA gmail.com Carol Matthews C00035 jnorris@gmail.com Angelafurt MD gmail.com Samantha Hernandez C00036 jesustaylor@hotmail.com Port Nicoleborough AR hotmail.com Jacob Mccoy C00037 eric78@hotmail.com Millerfurt VT hotmail.com Holly Arnold C00038 ythomas@hotmail.com Port Michaelstad MS hotmail.com Robert Haas C00039 angela55@hotmail.com Lake Michaelhaven AL hotmail.com Teresa Ward C00040 christianrogers@gmail.com New Michael TX gmail.com Francisco Horne C00041 pbarnes@hotmail.com Allisonhaven AK hotmail.com James Brooks C00042 hannasteven@yahoo.com South Garrettton IA yahoo.com Jenna Lewis C00043 ronnie19@hotmail.com South Johnville OK hotmail.com Margaret Sullivan C00044 ltran@rich.biz Port Danielle WY rich.biz Ashley Anderson C00045 dkhan@hotmail.com North Kara OK hotmail.com Matthew Lee C00046 josephpatterson@hotmail.com Barbaramouth MO hotmail.com Justin Collins C00047 fcalhoun@gmail.com Hallview OK gmail.com Wanda Morton C00048 floresvanessa@yahoo.com Lake Andrea MO yahoo.com Natalie Gentry C00049 kristinawalsh@gmail.com New Heatherside IA gmail.com Mike Harvey C00050 franklinalexis@hotmail.com Lopezfurt CO hotmail.com Mariah Wright C00051 millerjennifer@yahoo.com Anthonymouth CO yahoo.com Frank Phillips C00052 kevin81@hotmail.com Chapmanstad MS hotmail.com Scott Mathews C00053 zbarnett@hotmail.com Jacobville AR hotmail.com Kevin Harris C00054 lisasullivan@barnett.com North Joshua DE barnett.com Patrick Butler C00055 qfoley@hotmail.com Bishopview NE hotmail.com Joshua Kaufman C00056 cruzkristen@hotmail.com Catherineberg WA hotma

### Removing Duplicates based on Primary key.
#### Primary Key: customer_id (unique key)

In [0]:
df.dropDuplicates(subset=['customer_id'])
df.limit(10).display()

customer_id email city state domains full_name C00001 rushjeff@ryan.org Johnsonmouth MS ryan.org Emily Mooney C00002 mccoykiara@kelly.com Stephenfort WY kelly.com Andrea Sellers C00003 rebeccamiller@yahoo.com South Stephenshire LA yahoo.com Craig Hayes C00004 lawrence05@campbell.info Chrisland ND campbell.info Bryan Scott C00005 carrie45@yahoo.com East Dennistown RI yahoo.com Sean Vasquez C00006 traceyramos@gmail.com North Matthew IN gmail.com Kevin Mccarthy C00007 scottallen@gmail.com Joneshaven VA gmail.com Amanda Doyle C00008 sullivanjeremy@horton-adams.com South Nathanfurt CT horton-adams.com Paul Campos C00009 dennis03@yahoo.com Kimberlyview MD yahoo.com Mary Green C00010 charles58@murillo.net West Hector OK murillo.net James Myers

## **Dividing Old Vs. New Records**

In [0]:
if init_load_flag == 0:
    df_old = spark.sql('''select DimCustomerKey, customer_id, create_date, update_date 
                       from databricks_etl_catalog.gold.DimCustomers''')  # assuming this table (DimCustomers) exists, it will be created below.

else:
    df_old = spark.sql('''select 0 DimCustomerKey, 0 customer_id, 0 create_date, 0 update_date 
                       from databricks_etl_catalog.silver.customer_silver where 1=0''')  # where 1=0; this only returns the column from schema. And we are putting 0 values to pseudo columns as they are not present in silver table


In [0]:
df_old.display()

DimCustomerKey customer_id create_date update_date 8589934593 C00001 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934594 C00002 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934595 C00003 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934596 C00004 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934597 C00005 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934598 C00006 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934599 C00007 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934600 C00008 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934601 C00009 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934602 C00010 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934603 C00011 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934604 C00012 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934605 C00013 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934606 C00014 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934607 C00015 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934608 C00016 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934609 C00017 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934610 C00018 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934611 C00019 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934612 C00020 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934613 C00021 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934614 C00022 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934615 C00023 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934616 C00024 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934617 C00025 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934618 C00026 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934619 C00027 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934620 C00028 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934621 C00029 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934622 C00030 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934623 C00031 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934624 C00032 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934625 C00033 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934626 C00034 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934627 C00035 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934628 C00036 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934629 C00037 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934630 C00038 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934631 C00039 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934632 C00040 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934633 C00041 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934634 C00042 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934635 C00043 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934636 C00044 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934637 C00045 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934638 C00046 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934639 C00047 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934640 C00048 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934641 C00049 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934642 C00050 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934643 C00051 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934644 C00052 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934645 C00053 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934646 C00054 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934647 C00055 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934648 C00056 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934649 C00057 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 8589934650 C00058 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z 85899

#### Renaming Columns of Old Records

In [0]:
df_old = df_old.withColumnRenamed("DimCustomerKey", "old_DimCustomerKey")\
                .withColumnRenamed("customer_id", "old_customer_id")\
                .withColumnRenamed("create_date", "old_create_date")\
                .withColumnRenamed("update_date", "old_update_date")

## **Applying Join with Old Records**

In [0]:
df_join = df.join(df_old, df.customer_id == df_old.old_customer_id, 'left')
df_join.display()

customer_id email city state domains full_name old_DimCustomerKey old_customer_id old_create_date old_update_date C00001 rushjeff@ryan.org Johnsonmouth MS ryan.org Emily Mooney 8589934593 C00001 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00002 mccoykiara@kelly.com Stephenfort WY kelly.com Andrea Sellers 8589934594 C00002 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00003 rebeccamiller@yahoo.com South Stephenshire LA yahoo.com Craig Hayes 8589934595 C00003 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00004 lawrence05@campbell.info Chrisland ND campbell.info Bryan Scott 8589934596 C00004 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00005 carrie45@yahoo.com East Dennistown RI yahoo.com Sean Vasquez 8589934597 C00005 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00006 traceyramos@gmail.com North Matthew IN gmail.com Kevin Mccarthy 8589934598 C00006 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00007 scottallen@gmail.com Joneshaven VA gmail.com Amanda Doyle 8589934599 C00007 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00008 sullivanjeremy@horton-adams.com South Nathanfurt CT horton-adams.com Paul Campos 8589934600 C00008 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00009 dennis03@yahoo.com Kimberlyview MD yahoo.com Mary Green 8589934601 C00009 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00010 charles58@murillo.net West Hector OK murillo.net James Myers 8589934602 C00010 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00011 anita65@gmail.com Houstonfurt AR gmail.com Jacob Le 8589934603 C00011 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00012 beardtravis@gmail.com East Jenniferview WI gmail.com Chad Banks 8589934604 C00012 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00013 jwood@gmail.com Lake Gregoryshire OR gmail.com James Martin 8589934605 C00013 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00014 lmoore@yahoo.com East Tiffanybury MS yahoo.com Thomas Hartman 8589934606 C00014 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00015 daniellowe@hotmail.com South Courtney SC hotmail.com Diane Harris 8589934607 C00015 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00016 amylam@collins.org Jesusburgh IA collins.org Brett Parker 8589934608 C00016 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00017 rhondaferguson@gmail.com West Loriborough GA gmail.com Angela Carter 8589934609 C00017 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00018 martinfrank@brooks.info Lake Joshuamouth OH brooks.info Darrell Chang 8589934610 C00018 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00019 russelltimothy@simpson-hunter.com East Anthonyland NY simpson-hunter.com Angie King 8589934611 C00019 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00020 rojassandra@hotmail.com South Oscar NV hotmail.com Juan Collins 8589934612 C00020 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00021 morgancraig@stephens.com South Charles ND stephens.com Brian Hawkins 8589934613 C00021 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00022 pshepherd@walker-kelly.com Harrisland TN walker-kelly.com Jeanne Hahn 8589934614 C00022 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00023 greg64@banks.com North Kara NM banks.com Jackie Stewart 8589934615 C00023 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00024 andreawilliams@yahoo.com Stewartport NM yahoo.com Heather Owens 8589934616 C00024 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00025 dawn65@yahoo.com Port Juliebury IN yahoo.com Christina Bennett 8589934617 C00025 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00026 rebecca20@yahoo.com Ortizshire WY yahoo.com Mark Harris 8589934618 C00026 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00027 ashley08@mckinney.info Mosleyburgh NM mckinney.info Brandy Juarez 8589934619 C00027 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00028 steven27@gmail.com North Gregoryfurt NM gmail.com Barry Baker 8589934620 C00028 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C

## **Seperating New Vs. Old Records**

In [0]:
df_new = df_join.filter(df_join['old_DimCustomerKey'].isNull())    # where all records have null values for old_DimCustomerKey
df_new.limit(10).display()

customer_id email city state domains full_name old_DimCustomerKey old_customer_id old_create_date old_update_date

In [0]:
df_old = df_join.filter(df_join.old_DimCustomerKey.isNotNull())    # as this df_old is already added into Gold Layer 
df_old.limit(10).display()

customer_id email city state domains full_name old_DimCustomerKey old_customer_id old_create_date old_update_date C00001 rushjeff@ryan.org Johnsonmouth MS ryan.org Emily Mooney 8589934593 C00001 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00002 mccoykiara@kelly.com Stephenfort WY kelly.com Andrea Sellers 8589934594 C00002 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00003 rebeccamiller@yahoo.com South Stephenshire LA yahoo.com Craig Hayes 8589934595 C00003 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00004 lawrence05@campbell.info Chrisland ND campbell.info Bryan Scott 8589934596 C00004 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00005 carrie45@yahoo.com East Dennistown RI yahoo.com Sean Vasquez 8589934597 C00005 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00006 traceyramos@gmail.com North Matthew IN gmail.com Kevin Mccarthy 8589934598 C00006 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00007 scottallen@gmail.com Joneshaven VA gmail.com Amanda Doyle 8589934599 C00007 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00008 sullivanjeremy@horton-adams.com South Nathanfurt CT horton-adams.com Paul Campos 8589934600 C00008 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00009 dennis03@yahoo.com Kimberlyview MD yahoo.com Mary Green 8589934601 C00009 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z C00010 charles58@murillo.net West Hector OK murillo.net James Myers 8589934602 C00010 2025-07-18T22:53:34.216Z 2025-07-18T22:53:34.216Z

## **Preparing df_old Record**

In [0]:
# Dropping all columns that aren't required
df_old = df_old.drop('old_customer_id', 'old_update_date')

# Renaming 'Old_DimCustomerKey' to 'DimCustomerKey'
df_old = df_old.withColumnRenamed("old_DimCustomerKey", "DimCustomerKey")

# Renaming old_create_date to create_date
df_old = df_old.withColumnRenamed("old_create_date", "create_date") 
df_old = df_old.withColumn("create_date", to_timestamp(col("create_date")))

# Recreating 'update_date' column with current timestamp
df_old = df_old.withColumn("update_date", current_timestamp())


In [0]:
df_old.display()

customer_id email city state domains full_name DimCustomerKey create_date update_date C00001 rushjeff@ryan.org Johnsonmouth MS ryan.org Emily Mooney 8589934593 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00002 mccoykiara@kelly.com Stephenfort WY kelly.com Andrea Sellers 8589934594 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00003 rebeccamiller@yahoo.com South Stephenshire LA yahoo.com Craig Hayes 8589934595 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00004 lawrence05@campbell.info Chrisland ND campbell.info Bryan Scott 8589934596 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00005 carrie45@yahoo.com East Dennistown RI yahoo.com Sean Vasquez 8589934597 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00006 traceyramos@gmail.com North Matthew IN gmail.com Kevin Mccarthy 8589934598 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00007 scottallen@gmail.com Joneshaven VA gmail.com Amanda Doyle 8589934599 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00008 sullivanjeremy@horton-adams.com South Nathanfurt CT horton-adams.com Paul Campos 8589934600 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00009 dennis03@yahoo.com Kimberlyview MD yahoo.com Mary Green 8589934601 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00010 charles58@murillo.net West Hector OK murillo.net James Myers 8589934602 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00011 anita65@gmail.com Houstonfurt AR gmail.com Jacob Le 8589934603 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00012 beardtravis@gmail.com East Jenniferview WI gmail.com Chad Banks 8589934604 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00013 jwood@gmail.com Lake Gregoryshire OR gmail.com James Martin 8589934605 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00014 lmoore@yahoo.com East Tiffanybury MS yahoo.com Thomas Hartman 8589934606 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00015 daniellowe@hotmail.com South Courtney SC hotmail.com Diane Harris 8589934607 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00016 amylam@collins.org Jesusburgh IA collins.org Brett Parker 8589934608 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00017 rhondaferguson@gmail.com West Loriborough GA gmail.com Angela Carter 8589934609 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00018 martinfrank@brooks.info Lake Joshuamouth OH brooks.info Darrell Chang 8589934610 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00019 russelltimothy@simpson-hunter.com East Anthonyland NY simpson-hunter.com Angie King 8589934611 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00020 rojassandra@hotmail.com South Oscar NV hotmail.com Juan Collins 8589934612 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00021 morgancraig@stephens.com South Charles ND stephens.com Brian Hawkins 8589934613 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00022 pshepherd@walker-kelly.com Harrisland TN walker-kelly.com Jeanne Hahn 8589934614 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00023 greg64@banks.com North Kara NM banks.com Jackie Stewart 8589934615 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00024 andreawilliams@yahoo.com Stewartport NM yahoo.com Heather Owens 8589934616 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00025 dawn65@yahoo.com Port Juliebury IN yahoo.com Christina Bennett 8589934617 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00026 rebecca20@yahoo.com Ortizshire WY yahoo.com Mark Harris 8589934618 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00027 ashley08@mckinney.info Mosleyburgh NM mckinney.info Brandy Juarez 8589934619 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00028 steven27@gmail.com North Gregoryfurt NM gmail.com Barry Baker 8589934620 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00029 irandall@camacho-smith.com Kaiserhaven OR camacho-smith.com Michael Johnson 8589934621 2025-07-18T22:53:34.216Z 2025-07-18T23:00:34.285Z C00030 cfuller@gmail.com Port Coltonton AL gmail.com Holly Collins 8589934622 202

## **Preparing df_new Records**

In [0]:
df_new.limit(10).display()

customer_id email city state domains full_name old_DimCustomerKey old_customer_id old_create_date old_update_date C00001 rushjeff@ryan.org Johnsonmouth MS ryan.org Emily Mooney null null null null C00002 mccoykiara@kelly.com Stephenfort WY kelly.com Andrea Sellers null null null null C00003 rebeccamiller@yahoo.com South Stephenshire LA yahoo.com Craig Hayes null null null null C00004 lawrence05@campbell.info Chrisland ND campbell.info Bryan Scott null null null null C00005 carrie45@yahoo.com East Dennistown RI yahoo.com Sean Vasquez null null null null C00006 traceyramos@gmail.com North Matthew IN gmail.com Kevin Mccarthy null null null null C00007 scottallen@gmail.com Joneshaven VA gmail.com Amanda Doyle null null null null C00008 sullivanjeremy@horton-adams.com South Nathanfurt CT horton-adams.com Paul Campos null null null null C00009 dennis03@yahoo.com Kimberlyview MD yahoo.com Mary Green null null null null C00010 charles58@murillo.net West Hector OK murillo.net James Myers null null null null

##### Removing columns like : old_DimCustomerKey, old_customer_id, old_create_date, old_update_date: because all having 'null' values. Creating new columns instead

In df_new, the column 'create_date' will have current_timestamp function to retrieve current date & time. As df_new are processed now unlike df_old which are already in gold layer existing.

In [0]:
# Dropping unnecessary columns that are not required now
df_new = df_new.drop('old_DimCustomerKey', 'old_customer_id', 'old_create_date', 'old_update_date')

# Recreting new columns "update_date" & "current_date" by using function current_timestamp()
df_new = df_new.withColumn("update_date", current_timestamp())
df_new = df_new.withColumn("create_date", current_timestamp())

df_new.display()


customer_id email city state domains full_name update_date create_date

#### Assigning surrogate key column to Data Frame

Surrogate Key: a pseudo/fake key that create in dimension & can easily apply joins between fact and dimension tables

Dim_Key: a surrogate key of our primary key [customer_id]

## **Surrogate Key - For 1**

Assigning dim surrogate key column to df_new

In [0]:
# Creating surrogate keys for primary keys
df_new = df_new.withColumn("DimCustomerKey",monotonically_increasing_id()+lit(1))   
df_new.display()


customer_id email city state domains full_name update_date create_date DimCustomerKey

## **Adding Max Surrogate Key**

In [0]:
if init_load_flag == 1:
    max_surrogate_key = 0  # max surrogate key assigning to 0

else:
  df_maxsur = spark.sql("select max(DimCustomerKey) as max_surrogate_key from databricks_etl_catalog.gold.DimCustomers")
  # Converting df_maxsk to a list (max_sk)
  max_surrogate_key = df_maxsur.collect()[0]['max_surrogate_key']   # here with collect function we can convert values (collected dataframe as df_maxsk) to a list
  

Adding surrogate keys monotronically as increasing in df_new now one by one.

In [0]:
# Adding the max_sk to the new records with increments
df_new = df_new.withColumn("DimCustomerKey", lit(max_surrogate_key)+col("DimCustomerKey"))  # For ex. 2000+1 , 2000+2, and so on.

## **Union of df_old & df_new**

In [0]:
df_final = df_new.unionByName(df_old)

In [0]:
df_final.display()

customer_id email city state domains full_name update_date create_date DimCustomerKey C00001 rushjeff@ryan.org Johnsonmouth MS ryan.org Emily Mooney 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934593 C00002 mccoykiara@kelly.com Stephenfort WY kelly.com Andrea Sellers 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934594 C00003 rebeccamiller@yahoo.com South Stephenshire LA yahoo.com Craig Hayes 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934595 C00004 lawrence05@campbell.info Chrisland ND campbell.info Bryan Scott 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934596 C00005 carrie45@yahoo.com East Dennistown RI yahoo.com Sean Vasquez 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934597 C00006 traceyramos@gmail.com North Matthew IN gmail.com Kevin Mccarthy 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934598 C00007 scottallen@gmail.com Joneshaven VA gmail.com Amanda Doyle 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934599 C00008 sullivanjeremy@horton-adams.com South Nathanfurt CT horton-adams.com Paul Campos 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934600 C00009 dennis03@yahoo.com Kimberlyview MD yahoo.com Mary Green 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934601 C00010 charles58@murillo.net West Hector OK murillo.net James Myers 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934602 C00011 anita65@gmail.com Houstonfurt AR gmail.com Jacob Le 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934603 C00012 beardtravis@gmail.com East Jenniferview WI gmail.com Chad Banks 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934604 C00013 jwood@gmail.com Lake Gregoryshire OR gmail.com James Martin 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934605 C00014 lmoore@yahoo.com East Tiffanybury MS yahoo.com Thomas Hartman 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934606 C00015 daniellowe@hotmail.com South Courtney SC hotmail.com Diane Harris 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934607 C00016 amylam@collins.org Jesusburgh IA collins.org Brett Parker 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934608 C00017 rhondaferguson@gmail.com West Loriborough GA gmail.com Angela Carter 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934609 C00018 martinfrank@brooks.info Lake Joshuamouth OH brooks.info Darrell Chang 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934610 C00019 russelltimothy@simpson-hunter.com East Anthonyland NY simpson-hunter.com Angie King 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934611 C00020 rojassandra@hotmail.com South Oscar NV hotmail.com Juan Collins 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934612 C00021 morgancraig@stephens.com South Charles ND stephens.com Brian Hawkins 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934613 C00022 pshepherd@walker-kelly.com Harrisland TN walker-kelly.com Jeanne Hahn 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934614 C00023 greg64@banks.com North Kara NM banks.com Jackie Stewart 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934615 C00024 andreawilliams@yahoo.com Stewartport NM yahoo.com Heather Owens 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934616 C00025 dawn65@yahoo.com Port Juliebury IN yahoo.com Christina Bennett 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934617 C00026 rebecca20@yahoo.com Ortizshire WY yahoo.com Mark Harris 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934618 C00027 ashley08@mckinney.info Mosleyburgh NM mckinney.info Brandy Juarez 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934619 C00028 steven27@gmail.com North Gregoryfurt NM gmail.com Barry Baker 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934620 C00029 irandall@camacho-smith.com Kaiserhaven OR camacho-smith.com Michael Johnson 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34.216Z 8589934621 C00030 cfuller@gmail.com Port Coltonton AL gmail.com Holly Collins 2025-07-18T23:02:56.16Z 2025-07-18T22:53:34

## **Upsert Table = Upload + Insert**

### SCD Type 1 : Overwrite

In [0]:
from delta.tables import DeltaTable

### **Merging files**

In [0]:

if spark.catalog.tableExists("databricks_etl_catalog.gold.DimCustomers"):
        # Saving data to gold folder created in Azure Data Lake Storage Gen2
    dlt_obj = DeltaTable.forPath(spark, "abfss://gold@databricksetldatastorage.dfs.core.windows.net/DimCustomers")

    # Now merging & upsert the df_final to a target table
    dlt_obj.alias("trg").merge(df_final.alias("src"), "trg.DimCustomerKey = src.DimCustomerKey")\
                        .whenMatchedUpdateAll()\
                        .whenNotMatchedInsertAll()\
                        .execute()
        

else:
    df_final.write.mode("overwrite")\
        .format("delta")\
        .option("path", "abfss://gold@databricksetldatastorage.dfs.core.windows.net/DimCustomers")\
        .saveAsTable("databricks_etl_catalog.gold.DimCustomers")


In [0]:
%sql
SELECT *
FROM databricks_etl_catalog.gold.dimcustomers

customer_id email city state domains full_name DimCustomerKey update_date create_date C00001 rushjeff@ryan.org Johnsonmouth MS ryan.org Emily Mooney 8589934593 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00002 mccoykiara@kelly.com Stephenfort WY kelly.com Andrea Sellers 8589934594 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00003 rebeccamiller@yahoo.com South Stephenshire LA yahoo.com Craig Hayes 8589934595 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00004 lawrence05@campbell.info Chrisland ND campbell.info Bryan Scott 8589934596 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00005 carrie45@yahoo.com East Dennistown RI yahoo.com Sean Vasquez 8589934597 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00006 traceyramos@gmail.com North Matthew IN gmail.com Kevin Mccarthy 8589934598 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00007 scottallen@gmail.com Joneshaven VA gmail.com Amanda Doyle 8589934599 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00008 sullivanjeremy@horton-adams.com South Nathanfurt CT horton-adams.com Paul Campos 8589934600 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00009 dennis03@yahoo.com Kimberlyview MD yahoo.com Mary Green 8589934601 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00010 charles58@murillo.net West Hector OK murillo.net James Myers 8589934602 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00011 anita65@gmail.com Houstonfurt AR gmail.com Jacob Le 8589934603 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00012 beardtravis@gmail.com East Jenniferview WI gmail.com Chad Banks 8589934604 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00013 jwood@gmail.com Lake Gregoryshire OR gmail.com James Martin 8589934605 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00014 lmoore@yahoo.com East Tiffanybury MS yahoo.com Thomas Hartman 8589934606 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00015 daniellowe@hotmail.com South Courtney SC hotmail.com Diane Harris 8589934607 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00016 amylam@collins.org Jesusburgh IA collins.org Brett Parker 8589934608 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00017 rhondaferguson@gmail.com West Loriborough GA gmail.com Angela Carter 8589934609 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00018 martinfrank@brooks.info Lake Joshuamouth OH brooks.info Darrell Chang 8589934610 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00019 russelltimothy@simpson-hunter.com East Anthonyland NY simpson-hunter.com Angie King 8589934611 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00020 rojassandra@hotmail.com South Oscar NV hotmail.com Juan Collins 8589934612 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00021 morgancraig@stephens.com South Charles ND stephens.com Brian Hawkins 8589934613 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00022 pshepherd@walker-kelly.com Harrisland TN walker-kelly.com Jeanne Hahn 8589934614 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00023 greg64@banks.com North Kara NM banks.com Jackie Stewart 8589934615 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00024 andreawilliams@yahoo.com Stewartport NM yahoo.com Heather Owens 8589934616 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00025 dawn65@yahoo.com Port Juliebury IN yahoo.com Christina Bennett 8589934617 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00026 rebecca20@yahoo.com Ortizshire WY yahoo.com Mark Harris 8589934618 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00027 ashley08@mckinney.info Mosleyburgh NM mckinney.info Brandy Juarez 8589934619 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00028 steven27@gmail.com North Gregoryfurt NM gmail.com Barry Baker 8589934620 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00029 irandall@camacho-smith.com Kaiserhaven OR camacho-smith.com Michael Johnson 8589934621 2025-07-18T23:03:56.003Z 2025-07-18T22:53:34.216Z C00030 cfuller@gmail.com Port Coltonton AL gmail.com Holly Collins 8589934622 202